### モデルの形式 (.ckpt/.safetensors) を相互変換するスクリプトです
#### SD2.x系付属の.yamlも併せて変換します
#### オプションでfp16として保存できます

以下のコードを上から順番に両方とも実行

In [ ]:
from google.colab import drive 
drive.mount("/content/drive")

In [ ]:
!pip install torch safetensors
!pip install pytorch-lightning
!pip install wget

以下のリンク等を任意のものに差し替えてから、以下のコードを上から順番に両方とも実行

In [ ]:
#@title <font size="-0">モデルをダウンロード</font>
#@markdown {Google Drive上のモデル名 or モデルのダウンロードリンク} をカンマ区切りで任意個指定
#@markdown - Drive上のモデル名の場合...My Driveに対する相対パスで指定
#@markdown - ダウンロードリンクの場合...Hugging Face等のダウンロードリンクを右クリック & リンクのアドレスをコピー & 下のリンクの代わりに貼り付け
import shutil
import urllib.parse
import urllib.request
import wget

models = "Specify_the_model_in_this_way_if_the_model_is_on_My_Drive.safetensors, https://huggingface.co/hakurei/waifu-diffusion-v1-4/resolve/main/wd-1-4-anime_e1.ckpt, https://huggingface.co/hakurei/waifu-diffusion-v1-4/resolve/main/wd-1-4-anime_e1.yaml" #@param {type:"string"}
models = [m.strip() for m in models.split(",")]
for model in models:
  if 0 < len(urllib.parse.urlparse(model).scheme): # if model is url
    wget.download(model)
  elif model.endswith((".ckpt", ".safetensors")):
    shutil.copy("/content/drive/MyDrive/" + model, "/content/" + model) # get the model from mydrive
  else:
    print(f"\"{model}\"はURLではなく、正しい形式のファイルでもありません")

In [ ]:
#@title <font size="-0">モデルを変換</font>
#@markdown 変換するモデルをカンマ区切りで任意個指定<br>
#@markdown 何も入力されていない場合は、読み込まれている全てのモデルが変換される
import os
import glob
import torch
import safetensors.torch

models = "wd-1-4-anime_e1.ckpt, wd-1-4-anime_e1.yaml" #@param {type:"string"}
as_fp16 = True #@param {type:"boolean"}
save_directly_to_Google_Drive = True #@param {type:"boolean"}
save_type = ".safetensors" #@param [".safetensors", ".ckpt"]

def convert_yaml(file_name):
  with open(file_name) as f:
    yaml = f.read()
  if save_directly_to_Google_Drive:
    os.chdir("/content/drive/MyDrive")
  is_safe = save_type == ".safetensors"
  yaml = yaml.replace(f"use_checkpoint: {is_safe}", f"use_checkpoint: {not is_safe}")
  if as_fp16:
    yaml = yaml.replace("use_fp16: False", "use_fp16: True")
    file_name = os.path.splitext(file_name)[0] + "-fp16.yaml"
  with open(file_name, mode="w") as f:
    f.write(yaml)
  os.chdir("/content")

if models == "":
  models = [os.path.basename(m) for m in glob.glob(r"/content/*.ckpt") + glob.glob(r"/content/*.safetensors") + glob.glob(r"/content/*.yaml")]
else:
  models = [m.strip() for m in models.split(",")]

for model in models:
  model_name, model_ext = os.path.splitext(model)
  if model_ext == ".yaml":
    convert_yaml(model)
  elif (model_ext != ".safetensors") & (model_ext != ".ckpt"):
    print("対応形式は.ckpt及び.safetensors並びに.yamlのみです\n" + f"\"{model}\"は対応形式ではありません")
  else:
    load_model = safetensors.torch.load_file if model_ext == ".safetensors" else torch.load
    save_model = safetensors.torch.save_file if save_type == ".safetensors" else torch.save
    # convert model
    with torch.no_grad():
      weights = load_model(model)
      if "state_dict" in weights:
        weights = weights["state_dict"]
      if as_fp16:
        model_name = model_name + "-fp16"
        for key in weights.keys():
          weights[key] = weights[key].half()
      if save_directly_to_Google_Drive:
        os.chdir("/content/drive/MyDrive")
      save_model(weights, model_name + save_type)
      os.chdir("/content")
      del weights

!reset

SD2.x系モデル等を変換する場合は、付属の設定ファイル (モデルと同名の.yamlファイル) も同時にダウンロード/変換しましょう

指定方法はモデルと同じです

メモリ不足でクラッシュする場合は、より小さいモデルを利用するか、有料のハイメモリランタイムを使用すること

標準では10GBまでのモデルを変換できます

モデルのリンク集: https://huggingface.co/models?other=stable-diffusion 等から好きなモデルを選ぼう